In [37]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [38]:
import pandas as pd
from sklearn.metrics.pairwise import cosine_similarity
import scoring
import helpers

In [39]:
resumes = pd.read_parquet('processed/resume_embeddings.parquet')

In [40]:
jobs = pd.read_parquet('processed/dice_job_descriptions_embeddings.parquet')

In [41]:
resumes

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                       extracted_skills  length  \
0     [Accounting, Ads, Advertising, Analytical skil...    5442   
1     [Adobe Photoshop, ADP, Asset Management, brand...    5572   
2     [Recruiting, FMLA/EEO/FLSA, HRIS Development, ...    7720   
3     [Type 50 wpm and 10-Key by touch, Microsoft pr...    2855   
4     [ADA, ADP, art, agency, benefits, Benefits Adm...    9172   
...                                                 ...     ...   
2479  [Secret Clearance, Stock Control, Management, ...    5533   
2480  [arbitration, agency, budgets, Budget, continu...    7108   
2481  [Active Directory, Hardware, Customer Service,...    2020   
2482  [Adobe, CPR, Customer Service, Customer Care, ...    5074   
2483  [Architectural Drafting, AutoCAD, Customer Ser...    5234   

                                         matched_skills  \
0     [accounting, create advertisements, outdoor ad...   
1     [Adobe Photoshop, asset management, maintain c...   
2     [recruit members, foreign affairs policy devel...   
3     [personnel management, customer service, resol...   
4     [create artwork, coaching techniques, coaching...   
...                                                 ...   
2479  [follow stock control instructions, operations...   
2480  [examine budgets, update budget, continuous im...   
2481  [hardware materials, customer service, manage ...   
2482  [customer service, maintain customer service, ...   
2483  [create architectural sketches, customer servi...   

                                 matched_skills_ordered  \
0     [accounting, company policies, conduct public ...   
1     [Adobe Illustrator, Adobe Photoshop, asset man...   
2     [Microsoft Access, desktop publishing, foreign...   
3     [customer service, personnel management, resol...   
4     [Microsoft Access, Microsoft Visio, coaching t...   
...                                                 ...   
2479  [communication, follow stock control instructi...   
2480  [Microsoft Visio, computer graphics, continuou...   
2481  [assemble windows, customer service, hardware ...   
2482  [Microsoft Access, chair a meeting, customer s...   
2483  [advise on safety measures, advise supervisors...   

                                       skill_embeddings  \
0     [-0.051119804, 0.051380936, -0.1956489, -0.000...   
1     [-0.013

In [42]:
resumes = resumes[~resumes['skill_embeddings'].isna()]

In [43]:
resumes = resumes.reset_index(drop=True)

In [44]:
jobs

advertiserurl  \
0      https://www.dice.com/jobs/detail/AUTOMATION-TE...   
1      https://www.dice.com/jobs/detail/Information-S...   
2      https://www.dice.com/jobs/detail/Business-Solu...   
3      https://www.dice.com/jobs/detail/Java-Develope...   
4      https://www.dice.com/jobs/detail/DevOps-Engine...   
...                                                  ...   
21995  https://www.dice.com/jobs/detail/Web-Designer-...   
21996  https://www.dice.com/jobs/detail/Senior-Front-...   
21997  https://www.dice.com/jobs/detail/QA-Analyst-Sa...   
21998  https://www.dice.com/jobs/detail/Tech-Lead%252...   
21999  https://www.dice.com/jobs/detail/C%2526%252347...   

                                 company  \
0      Digital Intelligence Systems, LLC   
1      University of Chicago/IT Services   
2                   Galaxy Systems, Inc.   
3                          TransTech LLC   
4                       Matrix Resources   
...                                  ...   
21995                     IAC Publishing   
21996                Omega Solutions Inc   
21997          San Francisco Health Plan   
21998                     IAC Publishing   
21999          Technology Resource Group   

                                employmenttype_jobstatus  \
0      C2H Corp-To-Corp, C2H Independent, C2H W2, 3 M...   
1                                              Full Time   
2                                              Full Time   
3                                              Full Time   
4                                              Full Time   
...                                                  ...   
21995                                          Full Time   
21996                                          Full Time   
21997                                          Full Time   
21998                                          Full Time   
21999                               Full Time, Full Time   

                                          jobdescription               jobid  \
0      Looking for Selenium engineers...must have sol...  Dice Id : 10110693   
1      The University of Chicago has a rapidly growin...  Dice Id : 10114469   
2      GalaxE.SolutionsEvery day, our solutions affec...  Dice Id : CXGALXYS   
3      Java DeveloperFull-time/direct-hireBolingbrook...  Dice Id : 10113627   
4      Midtown based high tech firm has an immediate ...  Dice Id : matrixga   
...                                                  ...                 ...   
21995   Company Description We are searching for a ta...  Dice Id : 10112803   
21996   CONTACT - priya@omegasolutioninc.com / 408-45...  Dice Id : 10289500   
21997  Do you take pride in your work knowing that th...  Dice Id : 10115761   
21998  Company Description What We Can Offer YouAs th...  Dice Id : 10112803   
21999  Experience in C/C++ ProgrammingDevelopment exp...  Dice Id : 90734436   

      joblocation_address                                           jobtitle  \
0             Atlanta, GA                           AUTOMATION TEST ENGINEER   
1             Chicago, IL                      Information Security Engineer   
2          Schaumburg, IL                       Business Solutions Architect   
3         Bolingbrook, IL  Java Developer (mid level)- FT- GREAT culture,...   
4             Atlanta, GA                                    DevOps Engineer   
...                   ...                                                ...   
21995         Oakland, CA                                       Web Designer   
21996   San Francisco, CA  Senior Front End Web Developer - Full Time at ...   
21997   San Francisco, CA                                         QA Analyst   
21998         Oakland, CA                               Tech Lead-Full Stack   
21999     Santa Clara, CA                                   C/C++ Programmer   

             postdate                                            shift  \
0          1 hour ago  Telecommuting not available|Travel not required   
1 

In [45]:
jobs = jobs[~jobs['skill_embeddings'].isna()]

In [46]:
jobs = jobs.reset_index(drop=True)

In [47]:
job_embeddings = jobs['skill_embeddings'].tolist()

In [48]:
resume_embeddings = resumes['skill_embeddings'].tolist()

In [49]:
job_embeddings = jobs['skill_embeddings'].tolist()

In [50]:
similarities = cosine_similarity(resume_embeddings, job_embeddings)

In [51]:
best_match_indices = similarities.argmax(axis=1)
best_match_scores = similarities.max(axis=1)

In [52]:
resumes['best_match_index'] = best_match_indices
resumes['best_match_score'] = best_match_scores
resumes['best_match_job_embedding'] = jobs.loc[best_match_indices, 'skill_embeddings'].values
resumes['best_match_job_skills'] = jobs.loc[best_match_indices, 'matched_skills'].values

In [53]:
resumes

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                       extracted_skills  length  \
0     [Accounting, Ads, Advertising, Analytical skil...    5442   
1     [Adobe Photoshop, ADP, Asset Management, brand...    5572   
2     [Recruiting, FMLA/EEO/FLSA, HRIS Development, ...    7720   
3     [Type 50 wpm and 10-Key by touch, Microsoft pr...    2855   
4     [ADA, ADP, art, agency, benefits, Benefits Adm...    9172   
...                                                 ...     ...   
2479  [Secret Clearance, Stock Control, Management, ...    5533   
2480  [arbitration, agency, budgets, Budget, continu...    7108   
2481  [Active Directory, Hardware, Customer Service,...    2020   
2482  [Adobe, CPR, Customer Service, Customer Care, ...    5074   
2483  [Architectural Drafting, AutoCAD, Customer Ser...    5234   

                                         matched_skills  \
0     [accounting, create advertisements, outdoor ad...   
1     [Adobe Photoshop, asset management, maintain c...   
2     [recruit members, foreign affairs policy devel...   
3     [personnel management, customer service, resol...   
4     [create artwork, coaching techniques, coaching...   
...                                                 ...   
2479  [follow stock control instructions, operations...   
2480  [examine budgets, update budget, continuous im...   
2481  [hardware materials, customer service, manage ...   
2482  [customer service, maintain customer service, ...   
2483  [create architectural sketches, customer servi...   

                                 matched_skills_ordered  \
0     [accounting, company policies, conduct public ...   
1     [Adobe Illustrator, Adobe Photoshop, asset man...   
2     [Microsoft Access, desktop publishing, foreign...   
3     [customer service, personnel management, resol...   
4     [Microsoft Access, Microsoft Visio, coaching t...   
...                                                 ...   
2479  [communication, follow stock control instructi...   
2480  [Microsoft Visio, computer graphics, continuou...   
2481  [assemble windows, customer service, hardware ...   
2482  [Microsoft Access, chair a meeting, customer s...   
2483  [advise on safety measures, advise supervisors...   

                                       skill_embeddings  \
0     [-0.051119804, 0.051380936, -0.1956489, -0.000...   
1     [-0.013

In [54]:
resumes['true_missing'] = resumes.apply(
    lambda row: list(set(row['best_match_job_skills']) - set(row['matched_skills'])),
    axis=1
)

In [55]:
preds = resumes.apply(
    lambda row: helpers.predict_missing(row, job_embeddings, jobs, 'matched_skills', 'skill_embeddings'),
    axis=1
)
resumes['difference'] = preds.apply(lambda x: x["difference"])
resumes['predicted_missing'] = preds.apply(lambda x: x["skills"])
resumes['predicted_missing_id'] = preds.apply(lambda x: x["id"])
resumes['predicted_missing_embedding'] = preds.apply(lambda x: x["embeddings"])

In [57]:
scoring.found_score(resumes['true_missing'].tolist(),resumes['predicted_missing'].tolist())

np.float64(0.6051736421583942)

In [58]:
scoring.unnecessary_score(resumes['true_missing'].tolist(),resumes['predicted_missing'].tolist())

np.float64(0.30850488129749315)

In [59]:
scoring.redundant_score(resumes['predicted_missing'].tolist(), resumes['matched_skills'].tolist())

np.float64(0.1741236436855792)

In [60]:
scoring.presence_score(resumes['true_missing'].tolist(), resumes['predicted_missing'].tolist())

0.9090177133655395

In [56]:
resumes['best_match_score'].mean()

np.float64(0.8267800212805207)

In [61]:
index = 0
print("Job Description")
print(resumes['best_match_job_skills'].iloc[index])
print()
print("Sample Resume")
print(resumes['matched_skills'].iloc[index])

Job Description
['services marketing' 'project management' 'perform data analysis'
 'graphic design' 'outdoor advertising' 'devise special promotions'
 'market research' 'carry out event management' 'manage budgets'
 'social media management']

Sample Resume
['accounting' 'create advertisements' 'outdoor advertising'
 'monitor billing procedures' 'manage budgets' 'customer service'
 'perform data analysis' 'documentation types' 'financial management'
 'maintain relationships with government agencies' 'hire human resources'
 'types of insurance' 'store design layout' 'services marketing'
 'medical terminology' 'office administration' 'manage payroll'
 'recruit personnel' 'company policies' 'hang advertising posters'
 'conduct public presentations' 'public relations' 'statistics'
 'manage website']


In [62]:
true_missing = set(resumes['best_match_job_skills'].iloc[index])-set(resumes['matched_skills'].iloc[index])

In [63]:
set(resumes['true_missing'].iloc[index])

{'carry out event management',
 'devise special promotions',
 'graphic design',
 'market research',
 'project management',
 'social media management'}

In [64]:
diff = resumes['best_match_job_embedding'].iloc[index] - resumes['skill_embeddings'].iloc[index]

In [65]:
diffs = cosine_similarity([diff], job_embeddings)

In [66]:
predicted_missing = set(jobs['matched_skills'].iloc[diffs.argmax()])

In [67]:
predicted_missing

{'project management', 'services marketing'}

In [68]:
true_missing.intersection(predicted_missing)

{'project management'}

In [69]:
predicted_missing-true_missing

{'services marketing'}

In [70]:
print(len(true_missing.intersection(predicted_missing)))
print(len(true_missing-predicted_missing))

1
5


In [71]:
true_missing.symmetric_difference(predicted_missing)

{'carry out event management',
 'devise special promotions',
 'graphic design',
 'market research',
 'services marketing',
 'social media management'}

In [72]:
resumes['true_missing'].tolist()

[['devise special promotions',
  'project management',
  'carry out event management',
  'market research',
  'social media management',
  'graphic design'],
 ['supplier management',
  'iconography',
  'execute email marketing',
  'digital media',
  'perform data analysis',
  'adobe creative suite'],
 ['apply strategic thinking',
  'project management',
  'office software',
  'interview techniques',
  'assess\xa0candidates',
  'solve problems',
  'social media management',
  'talent management strategies'],
 ['project management', 'solve problems'],
 ['apply change management',
  'communication',
  'perform data analysis',
  'improve business processes'],
 ['project management',
  'manage data',
  'chair a meeting',
  'oversee record management',
  'translate strategy into operation',
  'communicate with stakeholders',
  'perform data analysis',
  'conduct public presentations',
  'develop project schedule'],
 ['prepare presentation material', 'mentor individuals', 'resolve conflicts']